In [1]:
import pandas as pd

In [2]:
data = pd.read_csv("drugsComTest_raw.csv")

In [3]:
data['problem'] = data['condition'] +"\n" + data['review']

In [4]:
data = data[['drugName','condition','review','problem']]

In [5]:
data.shape

(53766, 4)

In [6]:
data = data[data['problem'].notna()]

In [7]:
data

drugName                     condition  \
0          Mirtazapine                    Depression   
1           Mesalamine  Crohn's Disease, Maintenance   
2              Bactrim       Urinary Tract Infection   
3             Contrave                   Weight Loss   
4      Cyclafem 1 / 35                 Birth Control   
...                ...                           ...   
53761        Tamoxifen     Breast Cancer, Prevention   
53762     Escitalopram                       Anxiety   
53763   Levonorgestrel                 Birth Control   
53764       Tapentadol                          Pain   
53765        Arthrotec                      Sciatica   

                                                  review  \
0      "I&#039;ve tried a few antidepressants over th...   
1      "My son has Crohn&#039;s disease and has done ...   
2                          "Quick reduction of symptoms"   
3      "Contrave combines drugs that were used for al...   
4      "I have been on this birth control for one cyc...   
...                                                  ...   
53761  "I have taken Tamoxifen for 5 years. Side effe...   
53762  "I&#039;ve been taking Lexapro (escitaploprgra...   
53763  "I&#039;m married, 34 years old and I have no ...   
53764  "I was prescribed Nucynta for severe neck/shou...   
53765                                      "It works!!!"   

                                                 problem  
0      Depression\n"I&#039;ve tried a few antidepress...  
1      Crohn's Disease, Maintenance\n"My son has Croh...  
2      Urinary Tract Infection\n"Quick reduction of s...  
3      Weight Loss\n"Contrave combines drugs that wer...  
4      Birth Control\n"I have been on this birth cont...  
...                                                  ...  
53761  Breast Cancer, Prevention\n"I have taken Tamox...  
53762  Anxiety\n"I&#039;ve been taking Lexapro (escit...  
53763  Birth Control\n"I&#039;m married, 34 years old...  
53764  Pain\n"I was prescribed Nucynta for severe nec...  
53765                            Sciatica\n"It works!!!"  

[53471 rows x 4 columns]

In [8]:
len(data['drugName'].unique())

2635

In [9]:
print(data['drugName'].unique())

['Mirtazapine' 'Mesalamine' 'Bactrim' ... 'Guarana' 'Maprotiline'
 'FluMist']


In [9]:
unique_drugs = data['drugName'].unique().tolist()

In [10]:
with open('unique_drugs.txt', 'w') as f:
    for drug in unique_drugs:
        f.write(f'"{drug}",')

In [33]:
from datasets import Dataset

comments_dataset = Dataset.from_pandas(data)

/home/bacancy/Medical/.venv/lib/python3.10/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


In [34]:
from transformers import AutoTokenizer, AutoModel
import torch 
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")

model_ckpt = "sentence-transformers/multi-qa-mpnet-base-dot-v1"
tokenizer = AutoTokenizer.from_pretrained(model_ckpt)
model = AutoModel.from_pretrained(model_ckpt)   
model.to(device)

def cls_pooling(model_output):
    return model_output.last_hidden_state[:, 0]

def get_embeddings(text_list):
    encoded_input = tokenizer(
        text_list, padding=True, truncation=True, return_tensors="pt"
    )
    encoded_input = {k: v.to(device) for k, v in encoded_input.items()}
    model_output = model(**encoded_input)
    return cls_pooling(model_output)

embeddings_dataset = comments_dataset.map(
    lambda x: {"embeddings": get_embeddings(x["problem"]).detach().cpu().numpy()[0]}
)

/home/bacancy/Medical/.venv/lib/python3.10/site-packages/transformers/tokenization_utils_base.py:1601: FutureWarning: `clean_up_tokenization_spaces` was not set. It will be set to `True` by default. This behavior will be depracted in transformers v4.45, and will be then set to `False` by default. For more details check this issue: https://github.com/huggingface/transformers/issues/31884
  warnings.warn(
Map: 100%|██████████| 53471/53471 [2:05:35<00:00,  7.10 examples/s]  


In [36]:
embeddings_dataset.save_to_disk("/home/bacancy/Medical/new_data")

Saving the dataset (1/1 shards): 100%|██████████| 53471/53471 [00:00<00:00, 356492.37 examples/s]


In [60]:
df_filtered = data[data['drugName'].str.startswith('E')]

In [59]:
df_filtered['drugName'].unique()

array(['Duloxetine', 'Depakote', 'Drospirenone / estradiol',
       'Depo-Provera', 'Desyrel', 'Desvenlafaxine',
       'Drospirenone / ethinyl estradiol', 'Doxylamine / pyridoxine',
       'Demerol', 'Dextromethorphan', 'Diazepam', 'Diphenhydramine',
       'Denosumab', 'Dulaglutide', 'Drysol', 'Divalproex sodium',
       'Doxycycline', 'Desogestrel / ethinyl estradiol', 'Duofilm',
       'Dicyclomine', 'Dexmethylphenidate', 'Diltiazem', 'Dapsone',
       'Dalfampridine', 'Dilantin', 'Dienogest / estradiol', 'Diclofenac',
       'Donnatal', 'Depakote ER', 'Donepezil', 'Dulcolax', 'Dulera',
       'Dapagliflozin', 'Duexis', 'Differin', 'Doxepin', 'Docosanol',
       'Diclegis', 'Desloratadine',
       'Drospirenone / ethinyl estradiol / levomefolate calcium', 'Duac',
       'Deplin', 'Doryx', 'Dilaudid', 'Dimenhydrinate', 'Delsym',
       'Denavir', 'D.H.E. 45', 'Disulfiram', 'Droperidol', 'Dasatinib',
       'Dextrostat', 'Dymista', 'Dextroamphetamine', 'DDAVP Rhinal Tube',
       'Da

In [42]:
arr  = data['c'].unique()

In [49]:
arr.tolist()

['Mirtazapine',
 'Mesalamine',
 'Bactrim',
 'Contrave',
 'Cyclafem 1 / 35',
 'Zyclara',
 'Copper',
 'Amitriptyline',
 'Methadone',
 'Levora',
 'Paroxetine',
 'Miconazole',
 'Belviq',
 'Seroquel',
 'Ambien',
 'Nuvigil',
 'Chantix',
 'Microgestin Fe 1 / 20',
 'Klonopin',
 'Ciprofloxacin',
 'Trazodone',
 'EnteraGam',
 'Aripiprazole',
 'Cyclosporine',
 'Oxybutynin',
 'Lurasidone',
 'Clonazepam',
 'Ciclopirox',
 'Sodium oxybate',
 'Lamotrigine',
 'Blisovi Fe 1 / 20',
 'Ivermectin',
 'Suprep Bowel Prep Kit',
 'Movantik',
 'Actos',
 'Duloxetine',
 'NuvaRing',
 'Escitalopram',
 'Tesamorelin',
 'Campral',
 'Gabapentin',
 'Levonorgestrel',
 'Aubra',
 'Plan B One-Step',
 'Ethinyl estradiol / etonogestrel',
 'Microgestin Fe 1.5 / 30',
 'Wellbutrin',
 'Benzoyl peroxide / clindamycin',
 'Etonogestrel',
 'Nitrofurantoin',
 'Ortho Tri-Cyclen Lo',
 'Tamsulosin',
 'Tofacitinib',
 'Cryselle',
 'Amphetamine / dextroamphetamine',
 'Clindamycin',
 'Pramipexole',
 'Skyla',
 'Lastacaft',
 'Effexor XR',
 'Nife